# **VZ Intern Hackathon**

**Background:** Fixed wireless access, or FWA, is a type of 5G or 4G LTE wireless technology that enables fixed broadband access using radio frequencies instead of cables. FWA can be used to connect homes and businesses to the internet.

**Problem Statement:** Given a list of addresses that need to be served with 5G and a list of possible antenna locations, propose an efficient methodology to decide how to serve the customers based on most customers covered with the highest speeds and lowest cost of solution. There are 5 types of antenna, each with different coverage, cost, and throughput:

Antenna Type&emsp;&emsp;&emsp;&emsp;        Range(ft.)&emsp;&emsp;&emsp;&emsp;      Throughput(Mbps)&emsp;&emsp;&emsp;&emsp;&emsp;&nbsp;&nbsp;&nbsp;        Cost

    T-1                 100                 500                 $1000
    T-2                 200                 400                 $2000
    T-3                 300                 300                 $3000
    T-4                 400                 200                 $4000
    T-5                 500                 100                 $5000


In [48]:
# import libraries
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from geopy.distance import distance
from geopy.geocoders import Nominatim
import folium
#from folium.plugins import BeautifyIcon
import branca

# initialize Nominatim (which means “name” in Latin) as a variable called geolocator => uses OpenStreetMap data to match addresses with geopgraphic coordinates
geolocator = Nominatim(user_agent = "Mapping App", timeout = 2)

# read in datasets
customer_df = pd.read_csv("potentialCustomers.csv")                     # set of customer addresses


antenna_df = pd.read_csv("possibleAntennaLocations.csv")                # set of potential locations for FWA antennas
#antenna_df

antenna_types = {'Type': ['T-1', 'T-2', 'T-3', 'T-4', 'T-5'], 'Range (ft.)': [100, 200, 300, 400, 500], 'Throughput (Mbps)': [500, 400, 300, 200, 100], 'Cost ($)': [1000, 2000, 3000, 4000, 5000]}
antenna_types = pd.DataFrame(data = antenna_types)
antenna_types


Type  Range (ft.)  Throughput (Mbps)  Cost ($)
0  T-1          100                500      1000
1  T-2          200                400      2000
2  T-3          300                300      3000
3  T-4          400                200      4000
4  T-5          500                100      5000

In [49]:
# mapping and visualizing customer addresses
def create_map_markers(row, map_name, color = 'red'):
    #folium.Marker(location=[row['LAT'], row['LONG']], icon = folium.Icon(color = "pink", icon = "fa-solid fa-house", prefix='fa'), popup = row['Address']).add_to(map_name)
    folium.Rectangle([(row['LAT'], row['LONG'])], popup = row['Address'], color = color).add_to(map_name)

scarsdale_map = folium.Map(location = [customer_df.LAT.mean(), customer_df.LONG.mean()], zoom_start = 13.5)
#scarsdale_map

customer_df.apply(create_map_markers, map_name = scarsdale_map, axis = 'columns')
antenna_df.apply(create_map_markers, map_name = scarsdale_map, color = 'blue', axis = 'columns')

# adding a legend
legend_html = '''
{% macro html(this, kwargs) %}
<div style="
    position: fixed; 
    bottom: 50px;
    left: 40px;
    width: 200px;
    height: 50px;
    z-index: 9999;
    font-size:12px;
    ">
    <p><a style="color: red; font-size: 120%; margin-left: 10px;">&bull;</a>&emsp;Customer Addresses</p>
    <p><a style="color: blue; font-size: 120%; margin-left: 10px;">&bull;</a>&emsp;Potential Antenna Locations</p>
</div>
<div style="
    position: fixed; 
    bottom: 50px;
    left: 40px;
    width: 200px;
    height: 50px; 
    z-index:9998;
    font-size:14px;
    background-color: #ffffff;

    opacity: 0.7;
    ">
</div>
{% endmacro %}
'''

legend = branca.element.MacroElement()
legend._template = branca.element.Template(legend_html)

folium.LayerControl().add_to(scarsdale_map)
scarsdale_map.get_root().add_child(legend)

scarsdale_map

**Approach:** Treating this as an optimization problem, we will attempt to search for the solution with lowest cost and highest coverage — while also taking the throughput of our service into account with respect to population density.

In [50]:
# copy of antenna_df to work with
antenna_selected = antenna_df.copy()

print(antenna_selected)

# copies of customer_df to work with
customer_uncovered = customer_df.copy()

print(customer_uncovered)


     Location Code                             Address        LAT       LONG
0              A-1    12 Brayton Rd Scarsdale NY 10583  41.014263 -73.788063
1              A-2    8 Berkeley Rd Scarsdale NY 10583  41.015926 -73.786278
2              A-3     3 Berwick Rd Scarsdale NY 10583  40.999424 -73.797485
3              A-4  101 Brewster Rd Scarsdale NY 10583  41.006466 -73.787865
4              A-5    1 Berkeley Rd Scarsdale NY 10583  41.016464 -73.787254
...            ...                                 ...        ...        ...
1572        A-1573     81 Brite Ave Scarsdale NY 10583  41.004482 -73.792915
1573        A-1574     82 Brite Ave Scarsdale NY 10583  41.004730 -73.792732
1574        A-1575        17 Oak Ln Scarsdale NY 10583  41.005318 -73.794418
1575        A-1576     6 Olmsted Rd Scarsdale NY 10583  41.001507 -73.798607
1576        A-1577   7 Parkfield Rd Scarsdale NY 10583  41.004322 -73.799057

[1577 rows x 4 columns]
     Location Code                             Addr

In [51]:
# initialize Best_Solution variable to hold best solution found so far, Best_Cost variable to hold cost of Best_Solution, Total_Throughput variable to hold throughput of Best_Solution
Best_Solution = None
Best_Cost = 1000000000000000
Best_Throughput = 0

print(Best_Solution)
print(Best_Cost)
print(Best_Throughput)


None
1000000000000000
0


In [52]:
antenna_selected['Customers Covered'] = pd.NA

# select antenna type for each possible antenna location and hold customer covered's info.
for i in range(len(antenna_df)):
    customer_count_100 = []
    customer_count_200 = []
    customer_count_300 = []
    customer_count_400 = []
    customer_count_500 = []

    input_coor = (antenna_df['LAT'][i], antenna_df['LONG'][i])
    for address, lat, long in zip(customer_df["Address"], customer_df["LAT"], customer_df["LONG"]):
        cust_coor = (lat, long)
        if distance(input_coor, cust_coor).ft <= 100:
            customer_count_100.append(address)
        if distance(input_coor, cust_coor).ft <= 200:
            customer_count_200.append(address)
        if distance(input_coor, cust_coor).ft <= 300:
            customer_count_300.append(address)
        if distance(input_coor, cust_coor).ft <= 400:
            customer_count_400.append(address)
        if distance(input_coor, cust_coor).ft <= 500:
            customer_count_500.append(address)

    if len(customer_count_100) >= 15:
        antenna_selected.loc[i, 'Type'] = 'T-1'
        antenna_selected.at[i, 'Customers Covered'] = customer_count_100
    elif len(customer_count_200) >= 15:
        antenna_selected.loc[i, 'Type'] = 'T-2'
        antenna_selected.at[i, 'Customers Covered'] = customer_count_200
    elif len(customer_count_300) >= 15:
        antenna_selected.loc[i, 'Type'] = 'T-3'
        antenna_selected.at[i, 'Customers Covered'] = customer_count_300
    elif len(customer_count_400) >= 15:
        antenna_selected.loc[i, 'Type'] = 'T-4'
        antenna_selected.at[i, 'Customers Covered'] = customer_count_400
    elif len(customer_count_500) >= 15:
        antenna_selected.loc[i, 'Type'] = 'T-5'
        antenna_selected.at[i, 'Customers Covered'] = customer_count_500
    else:
        antenna_selected.loc[i, 'Type'] = 'T-5'
        antenna_selected.at[i, 'Customers Covered'] = customer_count_500

antenna_selected
        
# for loop(s)?
    # For each combination of antennas deployed at potential locations:
        # calculate the coverage area of each antenna deployment and store them in list (Area_Coverage)
        # check if coverage area overlaps with other coverage areas:
            # if so, try different location
            # if not, add to coverage list

    # iterate through all customer addresses to ensure everyone is covered
        # if customer address is not covered, continue deploying antennas

    # iterate through each antenna deployment in Area_Coverage and calculate total cost based on antenna type used

    # iterate through each antenna deployment in Area_Coverage and sum up throughput for all covered customers

    # Update Best_Solution, Best_Cost, and Best_Throughput as necessary
#        if total_cost < Best_Cost or (total_cost == Best_Cost and total_throughput > Best_Throughput):
#            Best_Solution = antenna_deployment
#            Best_Cost = total_cost
#            Best_Throughput = total_throughput



Location Code                             Address        LAT       LONG  \
0              A-1    12 Brayton Rd Scarsdale NY 10583  41.014263 -73.788063   
1              A-2    8 Berkeley Rd Scarsdale NY 10583  41.015926 -73.786278   
2              A-3     3 Berwick Rd Scarsdale NY 10583  40.999424 -73.797485   
3              A-4  101 Brewster Rd Scarsdale NY 10583  41.006466 -73.787865   
4              A-5    1 Berkeley Rd Scarsdale NY 10583  41.016464 -73.787254   
...            ...                                 ...        ...        ...   
1572        A-1573     81 Brite Ave Scarsdale NY 10583  41.004482 -73.792915   
1573        A-1574     82 Brite Ave Scarsdale NY 10583  41.004730 -73.792732   
1574        A-1575        17 Oak Ln Scarsdale NY 10583  41.005318 -73.794418   
1575        A-1576     6 Olmsted Rd Scarsdale NY 10583  41.001507 -73.798607   
1576        A-1577   7 Parkfield Rd Scarsdale NY 10583  41.004322 -73.799057   

                                      Customers Covered Type  
0     [12 Brayton Rd Scarsdale NY 10583, 6 Brayton R...  T-4  
1     [8 Berkeley Rd Scarsdale NY 10583, 1 Berkeley ...  T-4  
2     [3 Berwick Rd Scarsdale NY 10583, 6 Berwick Rd...  T-4  
3     [101 Brewster Rd Scarsdale NY 10583, 103 Brews...  T-3  
4     [1 Berkeley Rd Scarsdale NY 10583, 2 Berkeley ...  T-3  
...                                                 ...  ...  
1572  [76 Brite Ave Scarsdale NY 10583, 83 Brite Ave...  T-3  
1573  [83 Brite Ave Scarsdale NY 10583, 84 Brite Ave...  T-3  
1574  [83 Brite Ave Scarsdale NY 10583, 14 Chesterfi...  T-4  
1575  [163 Fox Meadow Rd Scarsdale NY 10583, 154 Fox...  T-4  
1576  [1 Butler Rd Scarsdale NY 10583, 2 Butler Rd S...  T-4  

[1577 rows x 6 columns]

In [107]:
# copy of antenna_selected to work with
antenna_selected_copy = antenna_selected.copy()
antenna_selected_copy

antennas_to_delete = set()
antennas_with_customers = set()

for index, row in antenna_selected_copy.iterrows():
    customers_covered = set(row['Customers Covered'])
    if not customers_covered:
        antennas_to_delete.add(index)
    elif antennas_with_customers.intersection(customers_covered):
        antennas_to_delete.add(index)
    antennas_with_customers.update(customers_covered)

df_filtered = antenna_selected_copy.drop(antennas_to_delete)
print(df_filtered)


    Location Code                               Address        LAT       LONG  \
0             A-1      12 Brayton Rd Scarsdale NY 10583  41.014263 -73.788063   
1             A-2      8 Berkeley Rd Scarsdale NY 10583  41.015926 -73.786278   
2             A-3       3 Berwick Rd Scarsdale NY 10583  40.999424 -73.797485   
3             A-4    101 Brewster Rd Scarsdale NY 10583  41.006466 -73.787865   
40           A-41    152 Brewster Rd Scarsdale NY 10583  41.012218 -73.785301   
68           A-69    180 Brewster Rd Scarsdale NY 10583  41.015034 -73.783646   
98           A-99     48 Brewster Rd Scarsdale NY 10583  41.000355 -73.791016   
129         A-130      108 Brite Ave Scarsdale NY 10583  41.008408 -73.790047   
230         A-231         2 Brook Ln Scarsdale NY 10583  41.012249 -73.792557   
236         A-237        1 Butler Rd Scarsdale NY 10583  41.003887 -73.799858   
268         A-269    12 Cambridge Rd Scarsdale NY 10583  41.005798 -73.782417   
381         A-382        46 